# n-Pair Trident Scattering Process

In this file, we set up an n-pair trident scattering process. A trident
process looks like $k e^- \to e^- (e^- e^+)^n$.

You can download this file as a [jupyter notebook](trident.ipynb).

In [1]:
using QEDFeynmanDiagrams

We need QEDcore of the [QEDjl-project](https://github.com/QEDjl-project) for base
functionality and a process type, for which we can use the `Mocks` submodule
from QEDbase for this tutorial. Downstream, a `ScatteringProcess` from QEDprocesses.jl
could be used, for example.

In [2]:
using QEDcore
using QEDbase.Mocks

Let's decide how many pairs our trident should produce:

In [3]:
n = 2;

Now we setup the scattering process accordingly. We only consider a single spin/polarization
combination here. For an example with many spin and polarization combinations, refer to the
[n-photon Compton example](compton.md)

In [4]:
proc = QEDbase.Mocks.MockProcessSP(
    (Electron(), Photon()),                                                         # incoming particles
    (Electron(), ntuple(_ -> Electron(), n)..., ntuple(_ -> Positron(), n)...),     # outgoing particles
    (SpinUp(), PolX()),                                                             # incoming particle spin/pols
    (SpinUp(), ntuple(_ -> SpinUp(), 2 * n)...),                                    # outgoing particle spin/pols
)

QEDbase.Mocks.MockProcessSP{Tuple{Electron, Photon}, Tuple{Electron, Electron, Electron, Positron, Positron}, Tuple{SpinUp, PolarizationX}, NTuple{5, SpinUp}}((electron, photon), (electron, electron, electron, positron, positron), (spin up, x-polarized), (spin up, spin up, spin up, spin up, spin up))

The `number_of_diagrams` function returns how many valid Feynman diagrams
there are for a given process.

In [5]:
number_of_diagrams(proc)

252

Next, we can generate the DAG representing the computation for our scattering process'
squared matrix element. This uses `ComputableDAGs.jl`.

In [6]:
dag = graph(proc)

Graph:
  Nodes: Total: 943, QEDFeynmanDiagrams.ComputeTask_PropagatePairs: 60, QEDFeynmanDiagrams.ComputeTask_Pair: 60, 
         DataTask: 505, QEDFeynmanDiagrams.ComputeTask_SpinPolCumulation: 1, QEDFeynmanDiagrams.ComputeTask_CollectTriples: 1, 
         QEDFeynmanDiagrams.ComputeTask_CollectPairs: 60, QEDFeynmanDiagrams.ComputeTask_Propagator: 60, QEDFeynmanDiagrams.ComputeTask_TripleNegated: 150, 
         QEDFeynmanDiagrams.ComputeTask_BaseState: 7, QEDFeynmanDiagrams.ComputeTask_PairNegated: 9, QEDFeynmanDiagrams.ComputeTask_Triple: 30
  Edges: 1553
  Total Compute Effort: 0.0
  Total Data Transfer: 0.0
  Total Compute Intensity: 0.0


To continue, we will need [`ComputableDAGs.jl`](https://github.com/ComputableDAGs/ComputableDAGs.jl). Since `ComputableDAGs.jl` uses
`RuntimeGeneratedFunction`s as the return type of `ComputableDAGs.get_compute_function`, we need
to initialize it in our current module.

In [7]:
using ComputableDAGs
using RuntimeGeneratedFunctions
RuntimeGeneratedFunctions.init(@__MODULE__)

Now we need an input for the function, which is a `QEDcore.PhaseSpacePoint`.
For now, we generate random momenta for every particle. In the future, QEDevents
will be able to generate physical `PhaseSpacePoint`s.

In [8]:
psp = PhaseSpacePoint(
    proc,
    MockModel(),
    FlatPhaseSpaceLayout(TwoBodyRestSystem()),
    tuple((rand(SFourMomentum) for _ in 1:number_incoming_particles(proc))...),
    tuple((rand(SFourMomentum) for _ in 1:number_outgoing_particles(proc))...),
)

PhaseSpacePoint:
    process: QEDbase.Mocks.MockProcessSP{Tuple{Electron, Photon}, Tuple{Electron, Electron, Electron, Positron, Positron}, Tuple{SpinUp, PolarizationX}, NTuple{5, SpinUp}}((electron, photon), (electron, electron, electron, positron, positron), (spin up, x-polarized), (spin up, spin up, spin up, spin up, spin up))
    model: mock model
    phase space layout: FlatPhaseSpaceLayout{TwoBodyTargetSystem{Energy{2}}}(TwoBodyTargetSystem{Energy{2}}(Energy{2}()))
    incoming particles:
     -> incoming electron: [0.9111656914702335, 0.6875736946455682, 0.5483240165653146, 0.2778877227307165]
     -> incoming photon: [0.2155153546987597, 0.10420980388653134, 0.42803225489202756, 0.19492982404387105]
    outgoing particles:
     -> outgoing electron: [0.5358300939513326, 0.8108213755005578, 0.2970102337122945, 0.11689913597810586]
     -> outgoing electron: [0.8466718130911522, 0.6555330676948669, 0.49552889355642593, 0.9727005525730231]
     -> outgoing electron: [0.22287506028

With the DAG, the process, `RuntimeGeneratedFunctions` initialized, and an input type to use
we can now generate the actual computable function:

In [9]:
func = get_compute_function(
    dag, proc, cpu_st(), @__MODULE__; concrete_input_type = typeof(psp)
);

Finally, we can test that the function actually runs and computes something by
simply calling it on the `PhaseSpacePoint`:

In [10]:
func(psp)

0.010776506382836993

We can benchmark the execution speed too:

In [11]:
using BenchmarkTools
@benchmark func($psp)

BenchmarkTools.Trial: 10000 samples with 1 evaluation per sample.
 Range (min … max):  18.786 μs … 39.573 μs  ┊ GC (min … max): 0.00% … 0.00%
 Time  (median):     19.045 μs              ┊ GC (median):    0.00%
 Time  (mean ± σ):   19.261 μs ±  1.349 μs  ┊ GC (mean ± σ):  0.00% ± 0.00%

  ▄█▇▃                                                        ▁
  █████▅██▃▃▁▁▃▁▁▁▃▅▅▅▄▄▃▁▁▃▁▁▃▃▁▁▃▄▁▁▁▃▁▁▁▄▁▁▃▁▁▃▃▃▃▄▁▃▃▅▇██ █
  18.8 μs      Histogram: log(frequency) by time      27.6 μs <

 Memory estimate: 256 bytes, allocs estimate: 2.

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*